<a href="https://colab.research.google.com/github/componavt/wd_book/blob/master/programming_tasks/natural_disasters/vuleq_connect/vuleq_connect.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# This program draws earthquakes, volcanoes and the nearest connections between them at a certain distance on a map of the Earth according to the CSV files earthquakes_2023.csv and volcanoes_2023.csv

Эта программа отрисовывает на карте Земли землетрясения, вулканы и соединяет ближайшие пары на определенном расстоянии по данным из CSV-файлов earthquakes_2023.csv и volcanoes_2023.csv


For the program to work, you need two CSV files generated using SPARQL queries: https://w.wiki/AXz7 and https://w.wiki/AY2R

Для работы программы необходимо два CSV-файла, сгенерированные при помощи SPARQL-запросов: https://w.wiki/AXz7 и https://w.wiki/AY2R

In [4]:
import folium
import csv
import numpy as np
from geopy.distance import geodesic
from scipy.spatial import KDTree
import pprint # Pretty Print for objects

!wget https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/volcanoes_2023.csv
!wget https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/earthquakes_2023.csv

--2024-07-04 11:36:24--  https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/volcanoes_2023.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 76165 (74K) [text/plain]
Saving to: ‘volcanoes_2023.csv.1’

volcanoes_2023.csv. 100%[===================>]  74.38K  --.-KB/s    in 0.02s   

2024-07-04 11:36:24 (4.62 MB/s) - ‘volcanoes_2023.csv.1’ saved [76165/76165]

--2024-07-04 11:36:24--  https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/vuleq_connect/earthquakes_2023.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185

In [5]:
!head -n 3 volcanoes_2023.csv

volcanoLabel;location
Puy Pariou;Point(2.971484 45.796824)
Вануа-Лава;Point(167.466666666 -13.8)


In [6]:

m = folium.Map()
Buff_list1 = []
Buff_list2 = []
line_between_objects1 = []
line_between_objects2 = []
repeat_check1 = 0
repeat_check2 = 0
repeat_check11 = 0
repeat_check22 = 0

# Opening a CSV-file and processing it
with open("volcanoes_2023.csv", encoding='utf-8', newline='') as csvfile:
    reader1 = csv.DictReader(csvfile, delimiter=";")
    for row in reader1:
        # Puy Pariou;Point(2.971484 45.796824) -> popup;point(Buff_list1)
		    # Editing the original coordinates

        # Prints the nicely formatted dictionary
        pprint.pprint(row)


        popup = row['volcanoLabel']
        cords = row['location'].replace("Point(", "").replace(")", "")
        Lat = cords.split()
        Buff_list1.extend([float(Lat[0]), float(Lat[1])]) # Adding coordinates to buffer
        # Coordinate processing
        cor = tuple(Buff_list1)
        Buff_list1.clear()
        if (repeat_check1 == cor[0] and repeat_check2 == cor[1]):
            continue
        line_between_objects1.append((cor[1], cor[0]))
        folium.Circle(radius=500, location=[cor[1], cor[0]], popup=popup, tooltip='Volcano ' + popup, color="red").add_to(
            m)
        repeat_check1 = cor[0]
        repeat_check2 = cor[1]
# The same function is only for earthquakes CVS-file
with open("earthquakes_2023.csv", encoding='utf-8', newline='') as csvfile:
    reader2 = csv.DictReader(csvfile, delimiter=";")
    for row in reader2:
        popup = row['earthquakeLabel']
        cords = row['location'].replace("Point(", "").replace(")", "")
        Lat = cords.split()
        Buff_list2.extend([float(Lat[0]), float(Lat[1])])
        cor = tuple(Buff_list2)
        Buff_list2.clear()
        if (repeat_check11 == cor[0] and repeat_check22 == cor[1]):
            continue
        line_between_objects2.append((cor[1], cor[0]))
        folium.Circle(radius=500, location=[cor[1], cor[0]], popup=popup, tooltip='Earthquake ' + popup,
                      color="black").add_to(m)
        repeat_check11 = cor[0]
        repeat_check22 = cor[1]

# Drawing a line between two coordinates using K-Demension Trees
	# The used algorithm is described in "Maneewongvatana and Mount" 1999.
	# The general idea is that the  is a binary tree, each of whose nodes represents an axis-aligned hyperrectangle.
	# Each node specifies an axis and splits the set of points based on whether their coordinate along that axis is greater than or less than a particular value.
tree1 = KDTree(line_between_objects1) # Creating KDTree with the values of our coordinates
dist = 63 # Minimal distance for creating a line (63 the maximum distance at which an earthquake affects a volcano)
closest_points = tree1.query(line_between_objects2, k=1, distance_upper_bound=dist)[1]

closest_pairs_check_array = []
for i in range(len(line_between_objects1)):
    if closest_points[i] != len(line_between_objects1):
        eq_location = line_between_objects2[i]
        volcano_location = line_between_objects1[closest_points[i]]
        distance = geodesic(eq_location, volcano_location).kilometers
        if distance <= dist:
            closest_pairs_check_array.append((eq_location, volcano_location, distance))
#Drawing lines
for pair in closest_pairs_check_array:
    folium.PolyLine([pair[0], pair[1]], color="purple", weight=1, opacity=1).add_to(m)
# Saving the map
m

{'location': 'Point(2.971484 45.796824)', 'volcanoLabel': 'Puy Pariou'}
{'location': 'Point(167.466666666 -13.8)', 'volcanoLabel': 'Вануа-Лава'}
{'location': 'Point(-68.833333333 -19.15)', 'volcanoLabel': 'Ислуга'}
{'location': 'Point(145.836666666 17.601944444)',
 'volcanoLabel': 'Аламаган (вулкан)'}
{'location': 'Point(37.83 6.78)', 'volcanoLabel': 'Hobicha'}
{'location': 'Point(36.08 0.25)', 'volcanoLabel': 'Богория (вулкан)'}
{'location': 'Point(158.666666666 53.366666666)',
 'volcanoLabel': 'Арик (вулкан)'}
{'location': 'Point(2.92648 45.9702)', 'volcanoLabel': 'Puy de Montiroir'}
{'location': 'Point(147.91324 45.37698)', 'volcanoLabel': 'Богдан Хмельницкий'}
{'location': 'Point(2.95828 45.71166)', 'volcanoLabel': 'Puy de Lassolas'}
{'location': 'Point(10.518888888 6.199722222)', 'volcanoLabel': 'Mount Oku'}
{'location': 'Point(137.55361111 36.10638889)',
 'volcanoLabel': 'Mount Norikura'}
{'location': 'Point(3.85482 45.0584)', 'volcanoLabel': 'Mont Denise'}
{'location': 'Point(3.